In [ ]:
library(coloc)
library(locuscomparer)

# Test dataset

In [ ]:
# load test data
data(coloc_test_data)
attach(coloc_test_data) ## datasets D1, D2, D3 and D4

In [ ]:
# visualize dataset D3 and D4
par(mfrow=c(2,1))
plot_dataset(D3, main="Dataset D3")
plot_dataset(D4, main="Dataset D4")

coloc tests 5 hypotheses:\
H0 : no association\
H1 : association to trait 1 only\
H2 : association to trait 2 only\
H3 : association to both traits; distinct causal variants\
H4 : association to both traits; shared causal variant

coloc.abf assumes one causal variant per locus,\
coloc.susie assumes multiple causal variant per locus.

For example, the output PP.H0.abf is the posterior probability of hypothesis H0 given observed data and ABF assumption.

In [ ]:
# sample result using ABF
my.res <- coloc.abf(dataset1=D1, dataset2=D2)

In [ ]:
# in order to use coloc.susie to accommondate multiple causal variants,
# it is best to run SuSiE first and store the results before running coloc.susie
# since SuSiE can take a while to run.
# We'll use D3 and D4 for coloc.susie since these are designed to have multiple causal variants
susie_res_3 = runsusie(D3)
susie_res_4 = runsusie(D4)

In [ ]:
# visualize SuSiE PIPs
par(mfrow=c(2,1))
plot_dataset(D3, susie_obj=susie_res_3, alty=susie_res_3$pip, ylab="D3 SuSiE PIP")
plot_dataset(D4, susie_obj=susie_res_4, alty=susie_res_4$pip, ylab="D4 SuSiE PIP")

In [ ]:
# run coloc.susie
if(requireNamespace("susieR",quietly=TRUE)) {
  susie.res=coloc.susie(susie_res_3,susie_res_4)
  print(susie.res$summary)
}

# CAD example

In [ ]:
# read in data
eqtl <- read.table(file="Artery_Coronary_v7_eQTL_PHACTR1.txt", header=T, as.is=T)
gwas <- read.table(file="CAD_GWAS.txt", header=T, as.is=T)

In [ ]:
# visualize the locus with locuscomparer
gwas_fn="CAD_GWAS.txt"
eqtl_fn="Artery_Coronary_v7_eQTL_PHACTR1.txt"
marker_col="rs_id"
pval_col="pval_nominal"
options(repr.plot.width = 10, repr.plot.height = 5)
locuscompare(in_fn1=gwas_fn, in_fn2=eqtl_fn, title1="GWAS", title2="eQTL", 
             marker_col1= marker_col, pval_col1=pval_col, marker_col2=marker_col, pval_col2=pval_col)

In [ ]:
# view the dataset requirements
help(check_dataset)

In [ ]:
# merging the GWAS and eQTL data
input <- merge(eqtl, gwas, by="rs_id", all=FALSE, suffixes=c("_eqtl","_gwas"))
input <- input[complete.cases(input), ] # remove NA rows
# build datasets according to requirements
gwas_dataset = list(beta=input$slope_gwas, varbeta=input$slope_se_gwas^2, pvalues=input$pval_nominal_gwas, 
                    snp=input$rs_id, type="cc", S=0.33, N=10000)
eqtl_dataset = list(beta=input$slope_eqtl, varbeta=input$slope_se_eqtl^2, pvalues=input$pval_nominal_eqtl, 
                    snp=input$rs_id, type="quant", N = 776)
# run coloc.abf
cad.res <- coloc.abf(dataset1=gwas_dataset, dataset2=eqtl_dataset, MAF=input$maf)